In [1]:
from pymol import cmd
import py3Dmol

import pandas as pd

from openbabel import pybel

from rdkit import Chem
from rdkit.Chem import AllChem, Draw

import sys, os, random
sys.path.insert(1, 'utilities/')

from utils import getbox, generate_ledock_file, dok_to_sdf

import warnings
warnings.filterwarnings("ignore")

%config Completer.use_jedi = False

In [2]:
os.chdir('test/Reverse_Docking/')

In [3]:
targets=['3LM5','2O3P','6M89','6QCD']

In [4]:
for pdb_code in targets:
    cmd.fetch(code=pdb_code,type='pdb1')
    cmd.select(name='Prot',selection='polymer.protein')
    cmd.save(filename='clean_targets/'+pdb_code+'_clean.pdb',format='pdb',selection='Prot')
    cmd.delete('all')
    
    !../../bin/lepro_linux_x86 {'clean_targets/'+pdb_code+'_clean.pdb'}
    
    os.rename('pro.pdb','clean_targets/'+pdb_code+'_clean_H.pdb')

In [5]:
ligand='c1cc(c(cc1C2=C(C(=O)c3c(cc(cc3O2)O)O)O)O)O'

In [6]:
mol=pybel.readstring(string=ligand,format='smiles')
mol.title='Quercetin'
mol.make3D('mmff94s')
mol.localopt(forcefield='mmff94s', steps=500)
out=pybel.Outputfile(filename='Quercetin.mol2',format='mol2',overwrite=True)
out.write(mol)
out.close()

In [7]:
for clean_pdb in os.listdir('clean_targets/'):
    if 'H' in clean_pdb:
        !../../bin/fpocket -f {'clean_targets/'+clean_pdb} -d > {'targets_pockets/'+clean_pdb.split('_')[0] +'.csv'}

In [8]:
for file in os.listdir('targets_pockets/'):
    if 'csv' in file:
        
        rec='clean_targets/'+'{}_clean_H.pdb'.format(file.replace('.csv',''))
        
        pockets=pd.read_csv('targets_pockets/'+file,sep=' ',index_col=[0])
        pockets=pockets[pockets['volume']>=250]
        
        for p in pockets.index:
            
            path_to_pockets='clean_targets/'+file.replace('.csv','_clean_H_out/')
            pocket_pqr_file='pocket{}_vert.pqr'.format(p)
            
            cmd.load(filename=path_to_pockets+pocket_pqr_file,format='pqr',object=p)
        
            center,size=getbox(selection=p,extending=4.0,software='vina')
        
            cmd.delete('all')
            
            out='smina_outfiles/'+file.replace('.csv','_pock_{}.sdf'.format(p))
            
            !../../bin/smina -r {rec} -l {'Quercetin.mol2'} -o {out} --center_x {center['center_x']} --center_y {center['center_y']} --center_z {center['center_z']} --size_x {size['size_x']} --size_y {size['size_y']} --size_z {size['size_z']} --exhaustiveness 8 --num_modes 5 >> {'smina.log'}

In [9]:
view = py3Dmol.view(viewergrid=(2,2),linked=False)

view.removeAllModels()
view.setViewStyle({'style':'outline','color':'black','width':0.1})

position=[(0,0),(0,1),(1,0),(1,1)]
index=0
for rec_file in os.listdir('clean_targets/'):
    if 'H.pdb' in rec_file:
        view.addModel(open('clean_targets/'+rec_file,'r').read(),'pdb',viewer=position[index])
        Prot=view.getModel(viewer=position[index])
        Prot.setStyle({'cartoon':{'arrows':True, 'tubes':True, 'style':'oval', 'color':'white'}},viewer=position[index])
        view.addSurface(py3Dmol.VDW,{'opacity':0.8,'color':'white'},viewer=position[index])
        
        for result_file in os.listdir('smina_outfiles/'):
            if rec_file.split('_')[0] in result_file:
                poses=Chem.SDMolSupplier('smina_outfiles/'+result_file)
                color = ["#"+''.join([random.choice('0123456789ABCDEF') for j in range(6)])]
                for pose in poses:
                    p=Chem.MolToMolBlock(pose)
                    view.addModel(p,'mol',viewer=position[index])
                    z=view.getModel(viewer=position[index])
                    z.setStyle({},{'stick':{'color':color[0],'radius':0.05}})

        index=index+1
view.zoomTo()
view.show()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [11]:
for file in os.listdir('targets_pockets/'):
    if 'csv' in file:
        
        rec='clean_targets/'+'{}_clean_H.pdb'.format(file.replace('.csv',''))
        
        pockets=pd.read_csv('targets_pockets/'+file,sep=' ',index_col=[0])
        pockets=pockets[pockets['volume']>=250]
        
        for p in pockets.index:
            
            path_to_pockets='clean_targets/'+file.replace('.csv','_clean_H_out/')
            pocket_pqr_file='pocket{}_vert.pqr'.format(p)
            
            cmd.load(filename=path_to_pockets+pocket_pqr_file,format='pqr',object=p)
        
            X,Y,Z=getbox(selection=p,extending=4.0,software='ledock')
        
            cmd.delete('all')
            
            
            generate_ledock_file(receptor=rec,l_list=['Quercetin.mol2'],l_list_outfile='ligand.list',
                                 x=[X['minX'],X['maxX']],
                                 y=[Y['minY'],Y['maxY']],
                                 z=[Z['minZ'],Z['maxZ']],
                                 rmsd=1.0,
                                 n_poses=5,
                                 out='dock.in')
            
            
            !../../bin/ledock_linux_x86 {'dock.in'}
            
            os.rename('Quercetin.dok','ledock_outfiles/'+file.replace('.csv','_pock_{}.dok'.format(p)))

In [12]:
for file in os.listdir('ledock_outfiles/'):
    if 'dok' in file:
        dok_to_sdf(dok_file='ledock_outfiles/'+file,output='ledock_outfiles/'+file.replace('dok','sdf'))

In [13]:
view = py3Dmol.view(viewergrid=(2,2),linked=False)

view.removeAllModels()
view.setViewStyle({'style':'outline','color':'black','width':0.1})

position=[(0,0),(0,1),(1,0),(1,1)]
index=0
for rec_file in os.listdir('clean_targets/'):
    if 'H.pdb' in rec_file:
        view.addModel(open('clean_targets/'+rec_file,'r').read(),'pdb',viewer=position[index])
        Prot=view.getModel(viewer=position[index])
        Prot.setStyle({'cartoon':{'arrows':True, 'tubes':True, 'style':'oval', 'color':'white'}},viewer=position[index])
        view.addSurface(py3Dmol.VDW,{'opacity':0.8,'color':'white'},viewer=position[index])
        
        for result_file in os.listdir('ledock_outfiles/'):
            if rec_file.split('_')[0] in result_file and 'sdf' in result_file:
                poses=Chem.SDMolSupplier('ledock_outfiles/'+result_file)
                color = ["#"+''.join([random.choice('0123456789ABCDEF') for j in range(6)])]
                for pose in poses:
                    p=Chem.MolToMolBlock(pose)
                    view.addModel(p,'mol',viewer=position[index])
                    z=view.getModel(viewer=position[index])
                    z.setStyle({},{'stick':{'color':color[0],'radius':0.05}})

        index=index+1
view.zoomTo()
view.show()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol